<a href="https://colab.research.google.com/github/evgeny-kolonsky/Lab3_MW/blob/main/Lab3_MW.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

#Lab 3  Mechanical Waves

Evgeny Kolonsky 2024

v.0.1.2

In [13]:
import numpy as np
from scipy import linalg as LA
from matplotlib import pyplot as plt
from matplotlib.animation import FuncAnimation
from IPython.display import HTML

%matplotlib notebook

https://lpsa.swarthmore.edu/MtrxVibe/MatrixAll.html

https://cooperrc.github.io/computational-mechanics/module_05/03_Good_Vibrations.html#./02_Keep_it_steady.ipynb


Motion equataion for a system without energy losses due to friction in matrix form is
$$
M \ddot x + K x = F
$$
here $M$ - moment inertia matrix, $F$ - angle elastity matrix, $F$ -  external force moments vector, $x$ - coordinates (rotation angles) vector.

Boundary conditions

The left end is drived by external driver
$$
x_0(t) = \eta(t)
$$

Coordinates vector $x$
$$
x =  \begin{bmatrix}
      x_1 \\
      \vdots\\
      x_n \end{bmatrix} ,
$$

Inertia matrix $M$
$$
M =  \begin{bmatrix}
      J_1 &     \\
       &\ddots & \\
       &            & J_n
      \end{bmatrix} ,
$$
Elastity matrix $K$
$$
K =  \begin{bmatrix}
      2 k &  -k  &  &         \\
      -k  &  2k  & -k &          \\
         & -k   & 2k  & -k &         \\
      & & &\ddots & -k\\
      & &         & -k & 2 k
      \end{bmatrix}
$$

External forces (monents) vector $F$
$$
F =  k \begin{bmatrix}
      \eta(t) \\
      \vdots\\
      0 \end{bmatrix} ,
$$

If $E_i$ is eigenvectors  and $\lambda_i$  is eigenvalue of matrix $Z = M^{-1}  K$, then natural frequecnies are
$$
\omega_i = \sqrt\lambda_i \quad i = 1,\cdots, n.
$$.
A system without friction can be represented in canonical form with
$$
x = A E y, \quad = A E  
$$
where $y_j = e^{i \omega_j t}$ - canonical coordinates vector, $A$ - initial amlpitudes in canonical coordinates.

Getting amplitudes $A$ from initial coordinates$x(0)$:
$$
x(0) = A E, \\
A = x(0) E^{-1}
$$


Constants and parameters

In [19]:
# single rod
l = 456e-3 # length of bar
m = 42e-3 # mass of bar
J = m * l**2 / 12 # moment of inertia of bar

# the mechanical wave system
L = 920e-3 # length of the system
n = 72 # number of elements in rotational oscillations system
d = L / n # distance between bars

k = 1.02 # elastity coeff

v = d * np.sqrt(k/J)
print(f'wave velocity expected {v*100:.0f} cm/s')

wave velocity expected 17 cm/s


In [31]:
K = k * np.diag(np.ones(n) * 2, 0) + \
    np.diag(-np.ones(n-1)   , 1) +  \
    np.diag(-np.ones(n-1)   ,-1)

M = np.diag(np.ones(n) * J)

Z = LA.inv(M) @ K

X0 = np.zeros(n)
for i in range(12):
  X0[i] = 0.1 * np.sin(i/12 * np.pi)


lambdas, E = LA.eig(Z)
isort = np.argsort(lambdas.real)
lambdas = lambdas[isort]
E = E[:,isort]
omega = np.sqrt(lambdas)

A = X0 @ LA.inv(E) # amplitudes
freqs = np.real(omega) / 2 / np.pi

In [36]:
print(f'Natural frequencies from {np.min(freqs):.2f} Hz to {np.max(freqs):.2f} Hz')

Natural frequencies from 1.18 Hz to 11.86 Hz


In [22]:
def X(t):
    return   A * np.exp(1j * omega * t - t/2/tau) @ E

In [44]:
fig, ax = plt.subplots()
x = range(n)
tau = 1 # s - decay time
t_max = 5 # s
delta_t = 0.05 # s
N = int(t_max / delta_t)
t = np.linspace(0, t_max, N)
y = X(0)
bottom = 0
h_stem = ax.stem(x, y, bottom=bottom,  linefmt='-.')

def update(i):
    y = X(t[i])

    # markerline
    h_stem[0].set_ydata(y)
    h_stem[0].set_xdata(x)  # not necessary for constant x

    # stemlines
    h_stem[1].set_paths([np.array([[xx, bottom],
                                   [xx, yy]]) for (xx, yy) in zip(x, y)])

    # baseline
    h_stem[2].set_xdata([np.min(x), np.max(x)])
    #h_stem[2].set_ydata([bottom, bottom])  # not necessary for constant bottom

anim = FuncAnimation(fig, update, frames=range(1, N, 1), interval=delta_t)
anim.save('so.gif', dpi=80)
HTML(anim.to_jshtml())

<IPython.core.display.Javascript object>

/usr/local/lib/python3.10/dist-packages/matplotlib/cbook.py:1699: ComplexWarning: Casting complex values to real discards the imaginary part
  return math.isfinite(val)
/usr/local/lib/python3.10/dist-packages/numpy/ma/core.py:3387: ComplexWarning: Casting complex values to real discards the imaginary part
  _data[indx] = dval
/usr/local/lib/python3.10/dist-packages/matplotlib/collections.py:1448: ComplexWarning: Casting complex values to real discards the imaginary part
  else mpath.Path(np.asarray(seg, float))
/usr/local/lib/python3.10/dist-packages/matplotlib/cbook.py:1345: ComplexWarning: Casting complex values to real discards the imaginary part
  return np.asarray(x, float)
/usr/local/lib/python3.10/dist-packages/matplotlib/collections.py:1448: ComplexWarning: Casting complex values to real discards the imaginary part
  else mpath.Path(np.asarray(seg, float))
/usr/local/lib/python3.10/dist-packages/matplotlib/cbook.py:1345: ComplexWarning: Casting complex values to real discards t

In [39]:
plt.plot(t, [np.real(X(ti))[-1] for ti in t])

xright = np.array([np.real(X(ti))[-1] for ti in t])
plt.plot(t, xright)
t[xright>0.01]

array([ 6.01202405,  7.81563126,  9.81963928, 10.02004008])

In [ ]:
import numpy as np
import matplotlib.pyplot as plt
from matplotlib.animation import FuncAnimation
from IPython.display import HTML

fig, ax = plt.subplots()
x = np.linspace(0.1, 2*np.pi, 50)
y = np.cos(x)
bottom = 0
h_stem = ax.stem(x, y, bottom=bottom,  linefmt='-.')

def update(i):
    y = np.cos(x +  i/50)

    # markerline
    h_stem[0].set_ydata(y)
    h_stem[0].set_xdata(x)  # not necessary for constant x

    # stemlines
    h_stem[1].set_paths([np.array([[xx, bottom],
                                   [xx, yy]]) for (xx, yy) in zip(x, y)])

    # baseline
    h_stem[2].set_xdata([np.min(x), np.max(x)])
    h_stem[2].set_ydata([bottom, bottom])  # not necessary for constant bottom

anim = FuncAnimation(fig, update, frames=range(10, 110, 1), interval=1000)
anim.save('so.gif', dpi=80)
HTML(anim.to_jshtml())

<IPython.core.display.Javascript object>